Skript zum Kurs
# Computergestützte Datenauswertung
im Bachelorstudiengang Physik am Karlsruher Institut für Technologie (KIT)

U. Husemann (basierend auf Materialien von G. Quast, T. Ferber und U. Husemann)

Sommersemester 2024

# Kapitel 3: Digitale Signalverarbeitung

## Digitale Daten

<a name="messen"></a>
### Was ist Messen?
Um die Relevanz digitaler Daten in der modernen Physik zu vestehen, lohnt sich ein abstrakter Blick auf den Prozess des Messens. Um ein konkretes Beispiel vor Augen zu haben, können Sie sich unter der Messung immer die Bestimmung eines elektrischen Widerstands durch eine Strom-Spannungs-Kennlinie vorstellen.

In einer Messung wird eine Eingangsgröße gemessen, z. B. eine Länge oder Zeitspanne, ein Strom oder eine Spannung. Ziel der Messung ist eine physikalisch sinnvolle Ergebnisgröße sowie deren Unsicherheit. Um diese zu erhalten, sind einige Zwischenschritte notwendig:
1. Die Messung findet mit einem Messgerät bzw. einem **Sensor** statt. Als Physiker:innen ist es Ihre Aufgabe, den Sensor nicht als "black box" zu betrachten, sondern genau zu verstehen, wie er funktioniert. Zum Beispiel könnte eine Kalibration des Sensors notwendig sein.
1. Die Messung sollte ggf. **mehrfach wiederholt** werden. In diesem Kurs haben Sie bereits kennengelernt, wie sich dadurch die Messunsicherheit reduzieren lässt.
1. Das **Messsignal** ist dann die Antwort des verwendeten Messgeräts auf eine Eingangsgröße. Die meisten modernen Messgeräte sind elektronisch, und das Messsignal ist demnach häufig ein analoges elektrisches Signal, entweder ein Strom oder eine Spannung.  
1. Die meisten Messsignale werden heute mit dem Computer weiter verarbeitet. Dazu müssen die analogen elektrischen Signal in **digitale Signale** umgewandet werden. An diesem Punkt werden häufig auch Korrekturen der Daten vorgenommen, z. B. um die oben genannten Kalibration durchzuführen.
1. Die digitalen Signale werden dann entweder in Echtzeit weiter verarbeitet oder vor der weiteren Verarbeitung zwischengespeichert. Die Zwischenspeicherung erfolgt in **digitalen Dateiformaten**, die Sie in diesem Kapitel kennenlernen werden.
1. Die digitalen Signale werden am Computer ausgewertet, häufig mit Methoden der **statistischen Datenanalyse**. Ergebnisgröße und Unsicherheit ergeben sich dabei aus dem Vergleich der Signale mit einem physikalischen Modell (z. B. ohmsches Gesetz für den Zusammenhang zwischen Strom und Spannung bei einem elektrischen Widerstand). Das ist Gegenstand von Kapitel 4.

### Digitale Abtastung und Quantisierung
Analoge Signale sind **kontinuierlich**, sowohl als Funktion der Zeit als auch als Funktion des Signalwerts. Um ein analoges Signal in ein digitales Signal umzuwandeln, muss es sowohl in der Zeit als auch im Signalwert **diskretisiert** werden (siehe Codebeispiel):
- Mit der digitalen **Abtastung** (engl.: sampling) wird die Signalauslenkung zu bestimmten festen Zeitpunkten bestimmt. Dies geschieht häufig mit einer festen Taktrate (engl.: clock).
- Durch eine **Quantisierung** (engl.: quantization) wird der analoge Signalwert auf eine Ganzzahl mit $m$ Bits abgebildet. Dadurch ergeben sich $2^m - 1$ mögliche digitale Signalwerte.

In [ ]:
"""illustration of sampling and quantization of an analog signal"""
import numpy as np
import matplotlib.pyplot as plt

fig, ax =  plt.subplots( 2, 2, figsize=(12,8) )
tmin, tmax = -0.5, 6.5 

# analog signal is a sine wave
t = np.linspace( 0, 2*np.pi, 200 )
wave = np.sin(t)
ax[0][0].hlines( 0, tmin, tmax, linestyle="dashed" )
ax[0][0].plot( t, wave, label="Analog Signal" )
ax[0][0].set_xlabel( "$t$" )
ax[0][0].set_ylabel( "Continuous Signal Value" )
ax[0][0].set_xlim( tmin, tmax )
ax[0][0].legend()

# time discrete signal
n = np.linspace( 0, 6, 12 )
sample = np.sin(n)
ax[0][1].hlines( 0, tmin, tmax, linestyle="dashed" )
ax[0][1].stem( n, sample, label="Time Discrete Signal" )
ax[0][1].set_xlabel( "$n$" )
ax[0][1].set_ylabel( "Continuous Signal Value" )
ax[0][1].set_xlim( tmin, tmax )
ax[0][1].legend()

# analog signal quantized
step=0.2
quant = step*np.round( np.sin(t)/step )
ax[1][0].hlines( 0, tmin, tmax, linestyle="dashed" )
ax[1][0].stairs( quant[:-1], edges=t, label="Quantized Signal" )
ax[1][0].set_xlabel( "$t$" )
ax[1][0].set_ylabel( "Discrete Signal Value" )
ax[1][0].set_xlim( tmin, tmax )
ax[1][0].legend()

# time discrete signal quantized
discrete_quant = step*np.round( sample/step )
ax[1][1].hlines( 0, tmin, tmax, linestyle="dashed" )
ax[1][1].stem( n, discrete_quant, label="Time Discrete Quantized Signal" )
ax[1][1].set_xlabel( "$n$" )
ax[1][1].set_ylabel( "Discrete Signal Value" )
ax[1][1].set_xlim( tmin, tmax )
ax[1][1].legend()


plt.show()

#### Analog-Digital-Wandler
Geräte zur Abtastung und Quantisierung analoger Signal werden als **Analog-Digital-Wandler** (engl.: analog-to-digital converter, ADC) bezeichnet. Wichtige Kennzahlen für ADCs sind die Abtastfrequenz und die Auflösung in Bits. Im folgenden Codebeispiel wird ein sinusförmiges Signal mit einem 4-Bit-ADC und 10 Abtastungen pro Periode digitalisiert.

In [ ]:
"""illustration of the principle of signal sampling"""
"""UH after G. Quast's example code"""

import numpy as np, matplotlib.pyplot as plt
from  scipy import interpolate

mnx = 0.
mxx = 1.5*np.pi
nbins = 7
xplt = np.linspace(mnx, mxx, nbins+1) # range in x
nplt = nbins * (xplt-mnx)/(mxx-mnx)   # sample number - 1

xana = np.linspace( mnx, mxx, 200 )   # analog values
nana = nbins * (xana-mnx)/(mxx-mnx)
yana = np.sin( xana )

yplt = np.sin(xplt)

miny = min(yplt)
maxy = max(yplt)

# quantization
nbits = 4
step  = ( maxy - miny ) / 2**nbits
quant = step * np.round( yplt/step )

fig,ax = plt.subplots( figsize=(6,5) )
minyp = miny - 0.05*( maxy - miny )
maxyp = maxy + 0.05*( maxy - miny )
ax.set_xlim( 0., nbins+2 )
ax.set_ylim( minyp, maxyp )

# plot sampled curve
ax.plot( nana+1, yana, 'r--', label='Analog Signal')

# plot individual measurements as markers
ax.plot( nplt+1, quant, 'o', color='steelblue', label='Measurements (%d bits)' % nbits ) 

# indicate sampling points as vert. lines
ax.vlines( nplt+1, minyp, yplt, colors='steelblue', linestyles='--' )
    
# axis labels and legend
ax.set_xlabel( r'Sampling, $n = t \,\nu_s$', size='large' )
ax.set_ylabel( 'Value', size='large' )
ax.legend( numpoints=1, loc='best', prop={'size':12} )

plt.show()


Im obigen Beispiel liefert der ADC bei jeder Abtastung einen neuen Wert. Es ist aber auch möglich, Signal häufiger auszulesen. Diese Technik wird als Überabtastung (engl.: oversampling) bezeichnet. Man kann zeigen, dass sich dadurch (unkorreliertes) Rauschen im Vergleich zum Signal besser unterdrücken lässt und sich damit der Signal-Rauschabstand (engl.: signal-to-noise ratio, SNR) verbessert. Um den Effekt zu sehen probieren Sie obigen Code mit mehr Abtastpunkten (`nbins=20`) und geringer Auflösung (`nbits=3`) aus. 

>**Bemerkung: WKS-Abtasttheorem** 
>
>Die "passende" Abtastfrequenz für ein Signal mit einer Bandbreite (Differenz zwischen höchster und niedrigster Frequenz) von $\nu_\mathsf{max}$ ergibt sich aus dem Whittaker-Kotelnikov-Shannon-(WKS-)Abtasttheorem, in älterer Literatur auch Nyquist-Shannon-Abtasttheorem genannt. Es besagt, dass ein Signal der Bandbreite $\nu_\mathsf{max}$ aus äquidistanten Abtastwerten exakt rekonstruiert werden kann, wenn es mit einer Frequenz von mindestens $2\nu_\mathsf{max}$ abgetastet wird. Eine $n$-fache Überabtastung ist in diesem Zusammenhang eine Abtastung mit $2n\nu_\mathsf{max}$.

<a name="interpolation"></a>
### Interpolation
Wie aus den obigen Abbildungen zu sehen, besteht die beste Form der Darstellung digitaler Daten aus den einzelnen Datenpunkten – die Daten liegen ja nur für feste Zeitpunkte und mit der Auflösung des ADC vor. Es kann allerdings vorkommen, dass Zwischenwerte benötigt werden oder eine Verbindung oder **Interpolation** der Datenpunkt als grafisches Hilfsmittel sinnvoll ist ("to guide the eye"). Das ist insofern "gestattet" als analoge Signale sich zwischen zwei Abtastungen fast immer "glatt" verhalten (also ihre gedachten Funktionsgraphen stetig oder stetig differenzierbar sind). 

In Matplotlib erhalten Sie eine stetige Verbindung der diskreten Punkte, wenn Sie dem obigen Code folgende Zeilen (vor dem `plt.show()`) hinzufügen:
```
# connect points by straight line
ax.plot( nplt+1, quant, 'b--', label = 'Linear Interpolation' )  
```
Eine Interpolation mit **kubischen Splines**, d. h. stetig differenzierbaren Kurven aus Polynomstücken dritten Grades, wie im Kurs "Programmieren und Algorithmen" in Kapitel 9 eingeführt, bekommen Sie mit folgendem Code:
```
# cubic spline interpolation
cs_y = interpolate.UnivariateSpline( nplt, quant, s=0 )
xplt2 = np.linspace( -0.5, nbins+0.5, 200 )
ax.plot(xplt2+1, cs_y(xplt2), 'g-.', lw=2, label = 'Spline Interpolation')  
```
Probieren Sie es aus!

## Digitale Datenformate

### Daten und ihre Bedeutung
Um aus Daten etwas zu lernen, ist es wichtig deren **Bedeutung** zu kennen. Die wenigsten Daten sind selbsterklärend, fast immer sind zusätzliche Informationen nötig, die den Datensatz definieren. Dieser werden als **Metadaten** bezeichnet.

**Beispiel**: Sie haben im Praktikum mit dem Computer folgende Wertepaare aufgenommen:
```[5.26389273 4.11237443]
[5.64990981 6.31579031]
[3.31035396 2.72230292]
[5.11071304 4.74767761]
[4.98544977 4.13855549]
[5.76158099 6.21749092]
[5.05718426 6.16025656]
[5.40487497 4.37446221]
...
```
Nur wenn Sie sich zusätzlich notiert haben, welche Größen hier gemessen wurden und in welchen Einheiten, sind Sie in der Lage den Wertepaaren eine Bedeutung zuzuordnen. Beispielsweise könnte die erste Spalte eingestellte elektrische Spannungen in Volt darstellen und die zweite den bei dieser Spannung gemessenen Strom in Milliampere. Diese Metadaten sind also zusätzlich zu den Daten erforderlich, um die Daten interpretieren zu können.

>**Bemerkung**: Der **Stein von Rosette** ist ein historisches Beispiel zur Bedeutung von Daten. Der Stein von Rosette stammt aus hellenistischer Zeit und wurde 1799 in Ägypten wiederentdeckt. Der Stein war zentral bei Übersetzung der altägyptischen Hieroglyphen, deren Bedeutung im Europa des frühen 19. Jahrhunderts unbekannt war. Geholfen hat, dass auf dem Stein derselbe Text in drei verschiedenen Sprachen und Schriften verfasst war, darunter das bereits bekannte Altgriechisch. In diesem Beispiel war es erst möglich, etwas aus den Daten in den Hieroglyphen zu lernen, nachdem deren Bedeutung geklärt werden konnte.

>**Exkurs: Umgang mit Forschungsdaten** 
>
>Vertrauen in die Wissenschaft und ihre Resultate wird unter anderem dadurch erreicht, dass wissenschaftliche Ergebnisse jederzeit für andere Personen (zumindest im Prinzip) nachvollziehbar sein müssen. Die [Deutsche Forschungsgemeinschaft](https://www.dfg.de) (DFG), die wichtigste öffentliche Geldgeberin für Forschung in Deutschland, hat dazu Regeln aufgestellt, die fordern:
>- **Nach- und Weiternutzung** von Forschungsdaten muss ermöglicht werden.
>- Forschungsdaten müssen für **mindestens 10 Jahre geeignet archiviert** werden.
>
> Diese Regeln gelten selbstverständlich auch international. Beim Speichern von Forschungsdaten müssen die **FAIR-Prinzipien** erfüllt sein:
>- **Findable**: Daten sollen wieder auffindbar sein.
>- **Accessible**: Daten sollen langfristig zugänglich sein.
>- **Interoperable**: Daten sollen technisch nachnutzbar und mit anderen Datensätzen kombinierbar sein.
>- **Reusable**: Daten sollen analytisch und intellektuell wiederverwendbar sein.

### Übersicht digitale Datenformate
Einige gängige digitale Datenformate haben Sie bereits im Kurs "Programmieren und Algorithmen" kennengelernt (Vorlesung 12 im Wintersemester 2023/2024). In diesem Kurs wird diese Diskussion noch einmal aufgegriffen. Digitale Dateiformate lassen sich in Binär- und Textdateien einteilen:
- **Binärdateien** sind nur maschinenlesbar und ihre Kodierung ist häufig systemabhängig. Beispiele sind kompilierte Computerprogramme, Bild- und Audiodateien sowie komprimierte Dateiformate.
- **Textdateien** sind sowohl von Maschinen als auch von Menschen lesbar, wobei es aber unterschiedliche Standards der Zeichenkodierung gibt.

>Gängige Standards der **Zeichenkodierung** in Textdateien: 
>- **ASCII** (American Standard Code for Information Interchange) verwendet eine 7-Bit-Kodierung. Damit ergeben sich 128 Zeichen, davon sind 95 druckbar, die restlichen 33 Zeichen sind Steuerzeichen (z. B. Zeilenvorschub, Tabulator)
>- **ISO 8859-x**: Unter diesem ISO-Standard sind verschiedene Erweiterungen der ASCII-Kodierung auf 8 Bits zusammengefasst, um weitere Zeichen darstellen zu können. Die Kodierung ISO 8859-1 "Western" beinhaltet zum Beispiel Sonderzeichen für viele lateinische Alphabete der westlichen Welt, u. a. deutsche Umlaute. Davon gibt es auch Varianten, z. B. der Standard Windows-1252 (auch: ANSI) speziell für Microsoft Windows.
>- **UTF-8** (Universal Coded Character Set Transformation Format, kurz: Unicode): mit dieser Kodierung sind Schriftzeichen für alle Sprachen weltweit mit Byteketten variabler Länge (bis zu vier Bytes) darstellbar. Derzeit (2024) ist UTF-8 der de-facto-Standard für Zeichenkodierung im Internet.

#### Beispiel: CSV
**CSV** (engl.: comma-separated values) ist ein sehr gängiges Format für tabellarische Daten. Die Daten liegen als menschenlesbare Textdatei vor und besitzen in der Regel eine oder mehrere Kopfzeilen mit Metadaten. Die Handy-App [phyphox](https://phyphox.org) liefert z. B. folgenden Daten, wenn die drei Beschleunigungsmesser des Handys ausgelesen werden:
```
"Time (s)","X (m/s^2)","Y (m/s^2)","Z (m/s^2)"
0.000000000E0,1.621128845E-1,-1.346450043E0,1.007988876E1
1.002300000E-2,1.779798889E-1,-1.441951447E0,1.033151550E1
2.004599999E-2,2.393522644E-1,-1.292412415E0,1.030891251E1
3.006900000E-2,2.058219910E-1,-1.199306030E0,1.024020538E1
...
```
Die Kopfzeile liefert die Metadaten in Form der Größe und Einheit für jede Spalte. Die Spalten sind durch ein Trennzeichen (engl.: delimiter) separiert. Neben dem namensgebenden Komma könnte das auch ein Semikolon, Leerzeichen, Tabulator o.ä. sein. Das Format eignet sich somit besonders für Tabellen, also "flache" zweidimensionale Daten, die aus Zeilen und Spalten bestehen. Einfache Messgeräte im Praktikum, Handy-Apps wie phyphox oder Datenlogger verwenden häufig das CSV-Format. Hier bestehen die Daten wie in obigem Beispiel aus Gleitkommazahlen.

CSV-Dateien können z. B. in Tabellenkalkulationsprogrammen (Microsoft Excel, LibreOffice Calc, Apple Numbers...) eingelesen und abgespeichert werden. Auch in Python gibt es mehrere Möglichkeiten, solche Dateien zu lesen und zu schreiben, z. B. können CSV-Dateien mit `np.genfromtxt` direkt in NumPy-Arrays geladen werden:

In [ ]:
"""reading a CSV file is a one-liner in NumPy, using np.genfromtext()"""
import numpy as np

# read file with proper exception handling
filename = "data/Accelerometer.csv"

try:
    # use NumPy method to read CSV straight from a text file
    # arguments: file name, delimiter, number of header lines to be skipped
    data = np.genfromtxt( filename, 
                        delimiter=",", 
                        skip_header=1 )
    
    # print first five lines of file
    print( data[0:5] )

except Exception as e:
    print(f"Error: {e}")

Weitere Varianten der Arbeit mit CSV-Dateien finden Sie in Vorlesung 12 des Kurses "Programmieren und Algorithmen", z. B. mit dem Python-Modul `csv` oder in pandas. Auch das in Kapitel 4 vorgestellte Softwarewerkzeug für das physikalische Praktikum [`PhyPraKit`](ekpwww.etp.kit.edu/~quast/PhyPraKit/htmldoc/) beinhalten entsprechende Funktionen. Diese sind insbesondere dann nützlich, wenn die Messgeräte in physikalischen Praktikum international unübliche Datenformate ausgeben, z. B. mit Dezimalkomma anstatt Dezimalpunkt.

#### Selbstbeschreibende Dateiformate
In der Physik gehen Datenstrukturen häufig weit über das hinaus, was mit zweidimensionale Tabellen von Gleitkommazahlen sinnvoll darstellbar ist. Beispielsweise liefern die Kollisionen von Elementarteilchen, die an den Experimenten am Large Hadron Collider (LHC) am CERN aufgezeichnet werden,  Datensätze mit einer reichen hierarchischen Struktur. Diese beinhaltet häufig die rekonstruierten Eigenschaften aller der Kollision entstehenden Teilchen und ihrer Zerfallsprodukte.

Solche Datenstrukturen sind mit CSV-Dateien nicht sinnvoll realisierbar. In der Teilchenphysik werden speziell entwickelte eigenen binäre Dateiformate eingesetzt. Hier sollen nur selbstbeschreibende menschenlesbare (Text-)Dateiformate vorgestellt werden, die in der Physik auch vorkommen, z. B. als Konfigurationsdateien für Programme.
Diese Dateien besitzen ein Format, das mit speziellen **Markierungen** (engl.: tags) die Datenstruktur innerhalb der Datei beschreibt. Es gibt mehrere gängige **Auszeichnungssprachen** (engl.: markup languages), die solche Markierungen beinhalten.

>**Exkurs: Auszeichnungssprachen** 
>
>Auszeichnungssprachen kennzeichnen Daten anhand von Markierungen. Beispiele dafür sind:
>- **HTML** (hypertext markup language), die grundlegende Sprache für Webseiten. Beispielsweise wird in HTML eine Überschrift der ersten Hierarchiestufe mit folgendem Tag markiert: `<h1>Überschrift 1</h1>`
>- **$\LaTeX$**, die Standardsprache für zum Setzen wissenschaftlicher Texte. Eine Abschnittsüberschrift in $\LaTeX$ sieht wie folgt aus: `\section{Abschnittsüberschrift}`
>- **Markdown**, die Sprache für Textpassagen in Jupyter-Notebooks, in der auch dieses Skript verfasst ist, besitzt im Vergleich zu anderen Auszeichnungssprachen vereinfachte Tags. Eine Überschrift der ersten Hierarchiestufe wird in Markdown markiert mit: `# Überschrift 1`
>
> Diese Beispiele stehen im Gegensatz zum  **WYSIWYG-Ansatz** (engl.: what you see is what you get), der z. B. in Textverarbeitungsprogrammen wie Microsoft Word, Apple Pages oder LibreOffice Writer nach wie vor möglich ist: für eine Überschrift wird einfach ein Text mit größeren Schriftzeichen fettgedruckt. Häufig ist es besser, **Form und Inhalt von Dokumenten zu trennen**. Dazu geben die Nutzenden die Überschrift als Text vor und spezifizieren zusätzlich: "dieser Text ist eine Überschrift". Das Programm sorgt dann für einen passenden Textsatz. Dies ist sowohl in Auszeichnungssprachen (über Tags) als auch in modernen Textverarbeitungsprogrammen möglich.

Beispiele für gängige selbstbeschreibende Datenformate, die in Python gut unterstützt werden und auch darüber hinaus im Internet häufig verwenden werden, umfassen:
- **XML** (extensible markup language) bildet die Basis für HTML und erlaubt, eigene selbstbeschreibende Dateiformate mit eigenen Tags zu definieren, z. B.
```
      <Data>
            <Time>
                  <Value>1.002300000E-2</Value>
                  <Unit>s</Unit>
            </Time>
            <Accelerometer>
                  <Value Coord="x">1.7797988E-1</Value>
                  <Value Coord="y">-1.4419514E0</Value>
                  <Value Coord="z">1.0331515E1</Value>
                  <Unit>m/s^2</Unit>
            </Accelerometer>
            <Gyroscope>
                  …
            </Gyroscope>
      </Data>
```
- **JSON** (JavaScript Object Notation, Aussprache: Jason) ist das Format, in dem u. a. Jupyter-Notebooks abgespeichert werden – schauen Sie sich z. B. dieses Skript gern einmal mit einem Texteditor an. Auch Python-Dictionaries verwenden dieses Format. Das obige Beispiel in XML sieht in JSON wie folgt aus:
```
      {
            "Name" : Data,
            "Time" : 1.002300000E-2,
            "Unit Time": "s",
            "Accelerometer" :
            {
                  "x Value" : 1.7797988E-1,
                  "y Value" : -1.4419514E0,
                  "z Value" : 1.0331515E1,
                  "Unit" : "m/s^2"
            },
            "Gyroskop" :
            {
                  …
            },
      }
```
- **YAML** (YAML Ain't Markup Language) ist ein etwas kompakteres Format, das beispielsweise zur Konfiguration von Software verwendet wird, auch beim Analysewerkzeug [PhyPraKit](https://etpwww.etp.kit.edu/~quast/PhyPraKit/htmldoc/) im Praktikum. Das rekursive Akronym des Namens YAML entspricht dem Humor der Szene, in der das Format entstanden ist. Das obige Beispiel hat in YAML folgende Form:
```
      --- # Data
      Time: 0.010023
      Unit Time: s
      Accelerometer:
            x Value: 1.7797988E-1
            y Value: -1.4419514E0
            z Value: 1.0331515E1
            Unit: m/s^2
      Gyroscope:
            …
      ```

## Digitale Signalverarbeitung
Die rohen elektrischen Signale von Sensoren werden in der Regel [über mehrere Stufen aufbereitet](#messen), bevor sie endgültig am Computer ausgewertet werden. Bereits die analogen Strom- oder Spannungssignale können vor der Digitalisierung mit spezialisierter analoger Elektronik geeignet geformt werden (engl.: signal shaping). Aufgrund der größeren Flexibilität von Computercode  im Vergleich zu spezialisierter Elektronik und der hohen Leistungsfähigkeit moderner Computer verlagert sich ein immer größerer Anteil der Signalverarbeitung auf den Stufe nach der Digitalisierung. Techniken der **digitalen Signalverarbeitung** (engl.: digital signal processing, DSP) umfassen unter anderem:
- **Interpolation** zwischen bekannten Datenpunkte (siehe oben)
- **Frequenzanalyse**: Transformation von Zeitreihen in Frequenzspektren mittels Fouriertransformation (und umgekehrt bei der inversen Fouriertransformation)
- **Digitale Filterung** im Ortsraum, Zeitbereich oder Frequenzraum
- **Korrelationsanalyse**: Kreuzkorrelation und Autokorrelation

Die **Interpolation** digitaler Daten, also die Annäherung unbekannter Werte zwischen bekannten Datenpunkten, wurde bereits im Kurs "Programmieren und Algorithmen" behandelt (Kapitel 9). Codebeispiele zur linearen Interpolation und zur Interpolation mit kubischen Splines finden sich weiter oben in diesem Kapitel, im Abschnitt über [Abtastung und Quantisierung](#interpolation).

### Frequenzanalyse
Zeitabhängige physikalische Phänomene, wie z. B. Schwingungen und Wellen, lassen sich im **Zeitbereich** (engl.: time domain) oder äquivalent im **Frequenzraum** (engl.: frequency domain) darstellen.  Mathematisch lassen sich diese Phänomene als Funktionen $f(t)$ darstellen, die in einer Fourierreihe als Funktion von Vielfachen der Kreisfrequenz $\omega$ entwickelt werden:
$$
f(t) = \frac{a_0}{2} + \sum_{m=1}^\infty 
\big[
a_m \cdot \cos( m\cdot \omega t ) +
b_m \cdot \sin( m\cdot \omega t ) 
\big].
$$
In dieser Gleichung werden $a_m$ und $b_m$ als Fourierkoeffizienten zur Kreisfrequenz $\nu_m = m\omega/(2\pi)$ bezeichnet. Die Signalhöhe im Frequenzraum ist dann $A_m \equiv \sqrt{a_m^2 + b_m^2}$. Äquivalent lässt sich die Fourierreihe auch direkt mit komplexen Koeffizienten $c_m$ schreiben:
$$
f(t) = \sum_{m=0}^\infty 
c_m \exp\left[ i\,m\cdot\omega t\right].
$$

Digitale Signale im Zeitbereich bestehen aus eine Reihe von zeitlich geordneten diskreten Datenpunkten. Diese Reihe wird als **Zeitreihe** (engl.: time series) bezeichnet. Für solche Zeitreihen gibt es ein numerisch sehr effizientes Verfahren zur Fouriertransformation, das als **schnelle Fouriertransformation** (engl.: fast Fourier transform, FFT) bezeichnet wird. Die ersten Ideen dazu hatte Carl Friedrich Gauß schon Anfang des 19. Jahrhunderts, aber seit den 60er Jahren des 20. Jahrhunderts ist die FFT mit dem Algorithmus von James William Cooley und John Wilder Tukey weit verfügbar und wird allgemein als **einer der wichtigsten Computeralgorithmen überhaupt** angesehen. Sowohl in NumPy als auch in SciPy gibt es einfach zu verwendende FFT-Module (`numpy.fft` und `scipy.fft`).

Im folgenden Codebeispiel wurde eine menschliche Stimme mit der Handy-App [phyphox](phyphox.org) aufgezeichnet und als Zeitreihe im CSV-Format abgespeichert. Die CSV-Datei wird eingelesen und mittels des FFT-Moduls von NumPy in den Frequenzraum transformiert.

In [ ]:
"""FFT: fast Fourier transform"""
import numpy as np
import matplotlib.pyplot as plt
from scipy import signal

# read audio signal
data = np.genfromtxt('data/phyphox_voice.csv', delimiter=",", skip_header=1 )
t = data[:,0]    
x = data[:,1]
N = len(x) 
sampling = 48000 # match Phyphox's default sampling frequency: 48 kHz

# real-valued FFT routine from NumPy
fft  = np.fft.rfft( x )
freq = np.linspace( 0, 0.5*sampling, int( 0.5*N ) + 1 ) 

# plotting the results
fig,ax = plt.subplots( 2, 1, figsize=(12,8))

# plot time series
ax[0].plot( t, x )
ax[0].set_xlabel( r'$t$ (ms)' )
ax[0].set_ylabel( r'Signal height in time domain (arbitrary units)' )

# plot FFT of time series
ax[1].plot( freq, np.abs( fft ) )
ax[1].set_xlabel( r'$\nu$ (Hz)' )
ax[1].set_ylabel( r'Signal height in frequency domain (arbitrary units)' )
ax[1].set_xlim( 0, 0.1*sampling )

plt.show()

>**Exkurs: Die Mathematik hinter der FFT**
>
>Die FFT ist ein numerisch sehr effizientes Verfahren zur Fouriertransformation von Zeitreihen. Mathematisch beruht sie auf einer **diskreten Fouriertransformation** (DFT) und nutzt die **Periodizität der komplexen Exponentialfunktion** aus. Der wesentliche Trick von Cooley und Tukey basiert auf der Beobachtung, dass die DFT eines Datensatzes mit $2n$ Elementen in zwei DFTs von Datensätzen mit $n$ Elementen zerlegt werden kann. Diese Zerlegung wird rekursiv so lange angewendet, bis die Datensätze nur noch aus einzelnen Elementen bestehen. Schließlich können die Teilergebnisse wieder zu einer vollständigen Fouriertransformation mit $2n$ Elementen zusammengesetzt werden.
>
> Die diskrete Zeitreihe wird dargestellt als ein Vektor $(f_0,\dots,f_{2n-1})$. Die (komplexen) Fourierkoeffizienten $c_m$ für $m=0, \dots, 2n-1$ der Zeitreihe sind gegeben als
>$$
c_m = \sum\limits_{k=0}^{2n-1} f_k \exp\left[-\frac{2\pi i}{2n}mk\right].
>$$
>Jetzt kommt der Trick von Cooley und Tukey zum Einsatz: die Einträge $f_k$ werden in solche mit geraden und ungeraden Indizes aufgeteilt:
>$$
c_m =
\sum\limits_{k=0}^{n-1} f_{2k} \exp\left[-\frac{2\pi i}{2n}m(2k)\right] + 
\sum\limits_{k=0}^{n-1} f_{2k+1} \exp\left[-\frac{2\pi i}{2n}m(2k+1)\right].
>$$
>Mit den Definitionen $f'_k \equiv f_{2k}$ und $f''_k \equiv f_{2k+1}$ und Ausklammern des $k$-unabhängigen Teils des Exponenten der Exponentialfunktion lässt sich diese Gleichung in die Summe aus zwei Fourierkoeffizienten $c'_m$ und $c''_m$ für die Einträge mit geraden ($'$) und ungeraden ($''$) Indizes umschreiben:
>$$
c_m = 
\sum\limits_{k=0}^{n-1} f'_{k} \exp\left[-\frac{2\pi i}{n}mk\right] + 
\exp\left[-\frac{\pi i}{n}m\right] \cdot
\sum\limits_{k=0}^{n-1} f''_{k} \exp\left[-\frac{2\pi i}{n}mk\right].
>$$
>Jetzt sind noch die Fälle $m<n$ und $m\geq n$ zu unterscheiden:
>$$
c_m = \begin{cases}
c'_m + \exp\left[-\frac{\pi i}{n}m\right] c''_m & m < n,\\
c'_{m-n} - \exp\left[-\frac{\pi i}{n}(m-n)\right] c''_{m-n} & m \geq n.\\
\end{cases}
>$$
>Der Geschwindigkeitsvorteil ist jetzt sichtbar: wenn $c'_m$ und $c''_m$ für jeweils $m=0,\dots,n-1$ berechnet sind, werden dadurch zwei Fourierkoeffizienten der ursprünglichen Zeitreihe berechnet, $c_m$ und $c_{m+n}$. Bis auf den Zusatzaufwand für die Zerlegung hat sich der Rechenaufwand dadurch halbiert. Dieser Zerlegungsalgorithmus wird jetzt rekursiv angewendet. Idealerweise ist für eine FFT $n$ eine Potenz von Zwei. Ist das nicht der Fall, können weitere Datenpunkte einfach durch Auffüllen mit dem Wert Null (engl.: zero-padding) hinzugefügt werden. Der Algorithmus bleibt auch so der effizienteste Algorithmus für Fouriertransformationen.

### Digitale Filterung
Mit dem Begriff Filterung wird in der Signalverarbeitung das **absichtliche Verändern** von Daten unter Ausnutzung von **Vorwissen** über Signal und Untergrund bezeichnet. Ein Filter (Maskulinum in der Umgangssprache, aber Neutrum in der Fachsprache der Elektrotechnik!) verändert dabei abhängig von der Frequenz die Amplitude und/oder die Phase eines Signals. Klassische Filter, z. B. bei Audiosignalen, verändern den Frequenzgang:
- Ein **Tiefpassfilter** unterdrückt hohe Frequenzen und damit häufig das Rauschen.
- Ein **Hochpassfilter** unterdrückt niedrige Frequenzen, z. B. das 50-Hz-Brummen der Netzspannung.
- Ein **Bandpassfilter** kombiniert Tief- und Hochpass.

Filter werden z. B. eingesetzt zur **Glättung** von Signalen mit hohem Rauschanteil. Das Vorwissen, das dabei ausgenutzt wird, besteht darin, dass sich das Signal nur langsam innerhalb des Datensatzes ändert, während sich das Untergrundrauschen schneller ändert. Für Zeitreihen entspricht das genau dem oben erwähnten Tiefpassfilter. Klassische analoge Zeigerinstrumente führen diese Glättung aufgrund der Trägheit der Anzeige "automatisch" durch. In der digitalen Signalverarbeitung gibt es eine Reihe von Standardalgorithmen zur Glättung von Signalen. Ein einfach zu implementierendes Beispiel für einen Glättungsalgorithmus ist der **gleitende Mittelwert**. Ein digitales Signal, das aus diskreten Datenpunkten $y_i$ ($i=0,\dots,N$) besteht, wird dabei wie folgt in ein neues Signal $m_j$ gefiltert:
$$
m_j = \frac{1}{2k+1} \sum_{l = -k}^{k} y_{j+l}
$$
Das neue Signal $m_j$ besteht also aus dem arithmetischen Mittelwert über eine Filterbreite von $w=2k+1$ Werten – den Wert $y_i$ und jeweils $k$ Werten links und rechts davon. Vorsicht ist dabei geboten an den Rändern des Datensatzes: die Glättung ist für $j<k$ und $j>N-k$ undefiniert, das kann z. B. durch "zero padding", d. h. Ergänzen des Datensatzes mit Nullwerten am Rand, umgangen werden. Der Parameter $k$ (bzw. $w$) bestimmt bei der Bildung des gleitenden Mittelwerts also, wie stark das Signal geglättet wird. Er muss klein genug gewählt werden, um nicht die charakteristischen Eigenschaften des Signals zu verwischen und gleichzeitig groß genug, um das Rauschen so gut wie möglich zu unterdrücken. Für Zeitreihen entspricht die Wahl von $k$ der Wahl der inversen Grenzfrequenz des Filters, d. h. große $k$ entsprechen niedrigeren Grenzfrequenzen.

Im folgenden Codebeispiel soll eine Zeitreihe aus $N$ Datenpunkten gefiltert werden. Es handelt sich um eine verrauschte Schwingung mit Schwebung. Für den gleitenden Mittelwert wurde $k=2$ gewählt. Probieren Sie es gern mit anderen Werten aus!


In [ ]:
# -------- animated_convolutionFilter.py -----------------------
# Description: example showing how a convolution filter works
#  for
#      sliding average
#      peak finder
#
# Author:      G. Quast   Nov. 2016
# dependencies: Python 3 numpy, matplotlib.pyplot 
# last modified: U. Husemann, May 2021
#---------------------------------------------------------------

# add this Jupyter magic command to enable animation on some systems (needs ipympl installed)
%matplotlib ipympl

import sys, numpy as np, matplotlib.pyplot as plt
import matplotlib.animation as anim
 
# construct (rectangular) template shapes . . .
# . . . for sliding average
fwidth = 5
kwin=int(fwidth/2)
v = np.array([1. for i in range(0, 2*kwin+1)], dtype=np.float32 )
k = int(len(v)/2)

# define a signal
xmin, xmax = 0., 30.
N      = 250
xplt   = np.linspace( xmin, xmax, N )
signal = 0.5*np.sin(xplt)+0.25*np.sin(1.3*xplt)+0.25*np.sin(2.5*xplt)

# add some random (Gaussian) noise
rng = np.random.default_rng( 42 )
signal += 0.05 * rng.normal( size=N )

# define and plot initial graphics
fig = plt.figure(figsize=(10., 7.5))
ax = fig.add_subplot(1,1,1)
graph_init = ax.plot(xplt, signal, 'b-')
ax.set_ylabel('Amplitude')
ax.set_xlabel('Position')
ax.set_ylim( -1.1, 1.1 )

scale = (xmax-xmin)/N

# code relevant to parts of figure to animate
graph_signal, = ax.plot( [], [], 'g-', lw=2 )
graph_line,   = ax.plot( [], [], 'r-', lw=3 )
graph_box,    = ax.fill( [], [], color='r', alpha=0.1 )

def animate(n):
  i = n+k 
  signal[i]  = sum( v * signal[i-k:i+k+1] ) / (2*k+1)   
  graph_signal.set_data( xplt[k:i], signal[k:i] )
  graph_line.set_data( np.array( list(range(i-k, i+k+1)))*scale, v )
  graph_box.set_xy( [ [(i-k)*scale,-1], [(i+k)*scale,-1], [(i+k)*scale,1], [(i-k)*scale,1] ] )
  return graph_line, graph_signal, graph_box

ani = anim.FuncAnimation( fig, animate, frames=N-2*k, interval=30, repeat=False, blit=True )
plt.show()


Mathematisch lässt sich eine Filterung mit einem zeitlich konstanten Filter als **Faltung** (engl.: convolution) der Daten (z. B. der Zeitreihe) $y_i$ mit einer Fensterfunktion $f_i$ beschreiben:
$$
m_j = (f*y)_j \equiv \sum_{l = -\infty}^{+\infty}  f_{l} \cdot y_{j+l}.
$$
In vielen Fällen ist $f_l$ dabei nur für endlich viele Werte von $l$ ungleich Null. In der Elektrotechnik werden solche Filter als "Filter mit endlicher Impulsantwort" (engl.: finite impulse response, FIR) bezeichnet. Der **gleitende Mittelwert** ist ein solches FIR-Filter mit
$$
f_l = \begin{cases}
\frac{1}{2k+1} & -k \leq l \leq k, \\
0 & \textsf{sonst}.
\end{cases}
$$

Weitere Beispiele für einfache FIR-Filter:
- **Kantenfilter** zur Entdeckung von Kanten im Signal (engl.: edge filter). Der Filter hat die Form einer Stufe. Das gefilterte Signal besitzt die größte Auslenkung an Punkten mit Kanten, d. h. dort, wo eine starken Änderung des Signals zwischen zwei Datenpunkten erfolgt:
$$
f_l = \begin{cases}
-1 & -k \leq l < 0, \\
+1 &  0 \leq l \leq k, \\
0  &\textsf{sonst}.
\end{cases}
$$

- Filter zur Suche nach **Extremwerten** des Signals (engl.: peak filter), in Form eines Rechtecks. Das gefilterte Signal besitzt die größte positive (negative) Auslenkung an den Maxima (Minima) des Ursprungssignals:
$$
f_l = \begin{cases}
-1 & -2k  \leq l < -k, \\
+1 & -k \leq l < k, \\
-1 & k  \leq l \leq 2k, \\
0  &\textsf{sonst}.
\end{cases}
$$

In der Bildbearbeitung und der automatischen Mustererkennung am Computer lassen sich diese Filter zu zweidimensionalen Filtermatrizen verallgemeinern, mit denen z. B. Fotodaten geglättet und geschärft werden können oder Ränder von Objekten detektiert werden können.

### Korrelationsanalyse
Prozesse wie Schwingungen wiederholen sich in regelmäßigen zeitlichen Abständen, sie sind **periodisch**. Eine Zeitreihe von Messungen der Auslenkung einer Schwingung wiederholt sich damit (näherungsweise) ebenfalls periodisch. Eine Zeitreihe mit dieser Eigenschaft wird auch als **selbstähnlich** bezeichnet. Diese Eigenschaft der Selbstähnlichkeit lässt sich u. a. dazu verwenden, periodische Signale von nicht-periodischem Rauschen zu unterscheiden: Die Reihe von Auslenkungen des periodischen Signals zu unterschiedlichen Zeitpunkten innerhalb der Zeitreihe ist selbstähnlich. Das Rauschen zu einem gegebenen Zeitpunkt ist häufig aber unabhängig vom Rauschen zu allen anderen Zeitpunkten. Die **Autokorrelation** einer Zeitreihe, also die **Korrelation** einer Zeitreihe **mit sich selbst** zu zwei Zeitpunkten $t$ und $s$, bietet ein quantitatives Maß für die Selbstähnlichkeit. Für Funktionen des Ortes gibt es ein äquivalentes Maß der Selbstähnlichkeit der Funktion mit sich selbst an unterschiedlichen Orten $x$ und $y$, das als **Kreuzkorrelation** bezeichnet wird. 

>**Erinnerung: Erwartungswert, Varianz, Kovarianz, Korrelation**
>
> Der **Erwartungswert** (engl.: expected value, expectation value) einer diskreten Verteilung einer Zufallsvariable $x$ mit Werten $x_i$ (mit $i=1,\dots,n$), die eine Wahrscheinlichkeit $P(x_i)$ besitzen, ist das erste Moment der Verteilung. Er ist ein Lagemaß für die Verteilung und definiert als: 
>$$
\mathsf{E}[x] \equiv \sum\limits_{i=1}^n x_i P(x_i).
>$$
>Für kontinuierliche Zufallsvariable mit einer Wahrscheinlichkeitsdichte $f(x)$ ist der Erwartungswert definiert als
>$$
\mathsf{E}[x] \equiv \int x\cdot f(x)\,\mathsf{d}x.
>$$
> Die **Varianz** von $P(x_i)$ oder $f(x)$ ist definiert als das zweite zentrale Moment der Verteilung, d. h. der Erwartungswert der quadratischen Abweichung einer Zufallsvariable $x$ von ihrem Erwartungswert: 
>$$
\mathsf{V}[x] \equiv \sigma^2 \equiv \mathsf{E}[(x-\mathsf{E}[x])^2] 
= (\mathsf{kurze\,Rechnung}\dots) 
=  \mathsf{E}[x^2] - \mathsf{E}[x]^2.
>$$
> Die Größe $\sigma_x=\sqrt{\sigma^2}$ wird als **Standardabweichung** (engl.: standard deviation) der Verteilung bezeichnet.
>
> Für zwei Zufallsvariablen $x$ und $y$ ist die **Kovarianz** (engl.: covariance) definiert als der Erwartungswert des Produkts der Abweichungen von $x$ und $y$ von ihren Erwartungswerten:
>$$
\mathsf{Cov}(x,y) \equiv \sigma_{xy} \equiv \mathsf{E}\left[(x - \mathsf{E}[x])(y - \mathsf{E}[y])\right] 
= (\mathsf{kurze\,Rechnung}\dots)
= \mathsf{E}[xy] - \mathsf{E}[x]\mathsf{E}[y].
>$$
> Die Kovarianz von $x$ bzw. $y$ mit sich selbst ergibt die Varianz dieser Größen, also z. B. $\mathsf{Cov}(x,x) = \mathsf{V}[x]$.
>
> Häufig anschaulicher als die Kovarianz ist der pearsonsche **Korrelationskoeffizient** (engl.: correlation coefficient), auch als linearer Korrelationskoeffizient bezeichnet:
>$$
>\rho_{xy} \equiv \frac{\mathsf{Cov}(x,y)}{\sigma_x \sigma_y}.
>$$
>Im Korrelationskoeffizient wird die Kovarianz von $x$ und $y$ auf das Produkt der Standardabweichungen $\sigma_x \sigma_y$ normiert, er besitzt daher eine Wertebereich zwischen –1 und 1: $-1 \leq \rho_{xy} \leq 1$, mit folgenden ausgezeichneten Werten:
>$$
\rho_{xy} = \begin{cases}
0 & \textsf{$x$ und $y$ (linear) unkorreliert} \\
+1 & \textsf{$x$ und $y$ 100\% positiv (linear) korreliert}\\
-1 & \textsf{$x$ und $y$ 100\% negativ (linear) korreliert (auch: antikorreliert)}
\end{cases}
>$$


Analog zur Definition der Kovarianz ist die **Autokovarianz** zweier Glieder eine Zeitreihe $\mathbf{y}$ zu zwei Zeitpunkten  $t$ und $s$ definiert als
$$
\gamma(s,t)\equiv\mathsf{Cov}(y_t, y_s^*) \equiv
\mathsf{E}\big[ (y_t - \mathsf{E}[y_t]) 
(y_s - \mathsf{E}[y_s])^* \big]
= \mathsf{E}[y_t \cdot y_s^*] - \mathsf{E}[y_t] \cdot \mathsf{E}[y_s^*]
$$
(wobei diese Definition auch für komplexe $\mathbf{y}$ gültig ist, im weiteren werden wir aber immer reelle Zeitreihen betrachten). Analog zum pearsonschen Korrelationskoeffizienten ist die **Autokorrelation** der Glieder der Zeitreihe gegeben durch die Autokovarianz normiert auf die Standardabweichungen:
$$
\rho(s,t)\equiv\frac{\mathsf{Cov}(y_t, y_s^*)}{\sigma_t \sigma_s}
$$
Viele physikalische Prozesse sind **stationär**. Das bedeutet unter anderem, dass ihre Autokorrelation nicht von den absoluten Zeiten $t$ und $s$ abhängig ist, sondern nur vom **Zeitunterschied** (engl.: lag) $\tau \equiv s - t$. Wir nehmen weiterhin an, dass $\mathsf{E}[y_t]=\mathsf{E}[y_s]=0$, alle Glieder der Zeitreihe also um den Nullpunkt variieren. Diese Bedingung ist für periodische Prozesse wie Schwingungen leicht zu erreichen, indem der Nullpunkt der Auslenkung entsprechend verschoben wird. Damit kommen wir auf eine Definition der Autokorrelation, die häufig verwendet wird:
$$
\rho_\tau = \frac{\gamma_\tau}{\gamma_0} 
\textsf{ mit } \gamma_\tau = \sum_{k=0}^{N-\tau-1} y_k^* \,y_{k+\tau}
\textsf{ und } \gamma_0 = \mathsf{V}[\mathbf{y}] = \sigma^2
$$
Achtung: $\gamma_\tau$ wird in NumPy auch ohne die Normierung auf $\gamma_0$ als Autokorrelation bezeichnet - bitte lesen Sie die Dokumentation entsprechender Methoden immer genau durch.

#### Beispiel: Frequenzmessung mit Autokorrelation
Im folgenden soll die Technik der Autokorrelation zur Frequenzmessung eines stark verrauschten Signals eingesetzt werden. Wir erwarten, dass das Rauschen zu einem gegebenen Zeitpunkt unabhängig vom Rauschen an allen anderen Zeitpunkten ist. Damit ist das Rauschsignal nicht selbstähnlich und die Autokorrelation ist nur für einen Zeitunterschied von $\tau\approx0$ von Null verschieden. Im Gegensatz dazu ist das Signal selbstähnlich. Wir erwarten daher für die Autokorrelation des Signals dieselbe Periode wie für das Signal selbst. Eine Frequenzbestimmung mit Autokorrelation wird u. a. in Tonstudios eingesetzt beim Audioeffekt "Auto-Tune", bei dem die Tonhöhe von menschlichem Gesang in Echtzeit auf die mathematisch korrekte Tonhöhe angepasst werden kann.

In [ ]:
"""Example code using autocorrelation to measure frequency in noisy data"""

import numpy as np
import matplotlib.pyplot as plt
from scipy import signal

# generate signal
nt = 500
tmin, tmax = 0, 50
times = np.linspace( tmin, tmax, nt )
signal = np.sin( times + 0.5 ) 

# add square wave noise
rng = np.random.default_rng( 42 )
noise = rng.uniform( -0.5, 0.5, nt )
signal += noise

# autocorrelation using np.correlate: mode='full' yields mirrored autocorrelation function in addition
autocorr = np.correlate( signal, signal, mode='full' )
autocorr /= autocorr[nt-1] # normalize

# autocorrelation using scalar product
gsignal, gnoise = np.zeros( nt ), np.zeros( nt )
gsignal[0] = np.inner( signal, signal )
gnoise[0] = np.inner( noise, noise )
for i in np.arange( 1, nt ):
    gsignal[i] = np.inner( signal[:-i], signal[i:] )
    gnoise[i] = np.inner( noise[:-i], noise[i:] )
acsignal = gsignal/gsignal[0]
acnoise  = gnoise/gnoise[0]

# plot results
fig,ax = plt.subplots( 2, 2, figsize=(12,8))
ax[0][0].plot( times, noise )
ax[0][0].set_xlabel( r'$t$ (arbitrary units)' )
ax[0][0].set_ylabel( r'Amplitude (arbitrary units)' )

ax[0][1].plot( times, acnoise )
ax[0][1].set_xlabel( r'$\tau$  (arbitrary units)' )
ax[0][1].set_ylabel( r'Amplitude (arbitrary units)' )

ax[1][0].plot( times, signal )
ax[1][0].set_xlabel( r'$t$  (arbitrary units)' )
ax[1][0].set_ylabel( r'Amplitude (arbitrary units)' )

ax[1][1].plot( times, acsignal )
ax[1][1].set_xlabel( r'$\tau$ ( (arbitrary units)' )
ax[1][1].set_ylabel( r'Amplitude (arbitrary units)' )

plt.show()


In Python lässt sich eine Autokorrelation einfach selbst implementieren. Wie an obiger Definition zu sehen, besteht sie aus dem Skalarprodukt der Zeitreihe $\mathbf{y}$ mit einer um den Zeitunterschied $\tau$ verschobenen Version von sich selbst. Dies ist in der folgenden Animation illustriert:

In [ ]:
# script animate_autoCorrelation
''' calculation the autocorrelation function
    with animated illustration
.. author:: Guenter Quast <g.quast@kit.edu>
'''

# dependencies:  Python v3.12, numpy, matplotlib
# last modified: U. Husemann, March 2024
#--------------------------------------------------------------

# add this Jupyter magic command to enable animation on some systems (needs ipympl installed)
%matplotlib ipympl

import numpy as np, matplotlib.pyplot as plt, sys
import matplotlib.animation as anim

##### ---- main program starts here -----
if __name__ == "__main__":

	print(('\n*==* script ' + sys.argv[0]+' executing'))

	# read data
	data = np.genfromtxt('data/phyphox_voice.csv', delimiter=",", skip_header=1 )

	# use only the first 250 rows of data input
	t = data[:250,0]
	y = data[:250,1]
 
	N = len(y)  
	
	# generate and plot static part of figure
	fig = plt.figure( figsize=(10.,7.5) )
	ax1 = fig.add_subplot( 2,1,1 )
	ax2 = fig.add_subplot( 2,1,2 )
	ax1.grid( True )
	ax2.grid( True )
	
	ax1.set_title( 'Autocorrelation of a periodic signal', size='xx-large' )
	ax1.set_xlabel( 'Time (ms)' )
	ax2.set_xlabel( 'Time Difference (ms)' )
	ax1.set_ylabel( 'Amplitude')
	ax2.set_ylabel( r'Autocorrelation $\rho$' )
  	
	timetxt = ax1.text(0.3, 0.9, ' ', transform=ax1.transAxes,size='large', backgroundcolor='white')
                    	
	# plot dummy versions of all objects for later animation
	graph1,  = ax1.plot( t, y, '-', color='black' )
	graph1a, = ax1.plot( [], [], '-', color='blue', lw=2 )
	graph1b, = ax1.plot( [], [], '-', color='blue', lw=2 )
	graph1c  = ax1.axvline( color='darkred')
	graph2, = ax2.plot( t, np.zeros( len(t) ), '--', color='black', lw=1 )
  	
	ax2.set_ylim(-1.,1.)
	
	# variables for dynamic part   
	nrep = N-1 # number of repetitions	
	rho    = np.zeros( N )   # vector for autocorrelations (calulated in animate)
	rho[0] = np.inner( y, y )

	def animate(n):
    	# animation loop
		global rho
		
		i = n+1
		# calculate autocorrelation at i as inner product
		rho[i] = np.inner(y[i:], y[:-i])/rho[0] 
		
		# update animation objects
		graph1a.set_data( t[i:], y[:-i] )
		graph1b.set_data( t[i:], y[i:] )
		graph1c.set_xdata( [t[i]] ) # must be a sequence type, even for a single value
		graph2, = ax2.plot(t[:i], rho[:i], '-', color='darkred', lw=2)
		timestep='i=%i' %(i)
		timetxt.set_text(timestep)
		return graph1a, graph1b, graph1c, graph2, timetxt

	# excute animation (calls animate() nrep times every 30 ms)  
	ani=anim.FuncAnimation( fig, animate, frames=nrep, interval=50, repeat=False )
       
	# write an mp4 movie using the ffmpeg encoder (to be installed separately)
	#Writer = anim.writers[ 'ffmpeg' ]
	#writer = Writer( fps=30, bitrate=64000 )
	#ani.save( "autocorr.mp4", writer=writer )
	#plt.savefig( "autocorr.pdf")
                         
	plt.show()
